# 작업 내용
- 독자-독자 Doc2Vec
- 작가-작가 Doc2Vec

In [ ]:
# Doc2vec 실행을 위한 genism 설치
# !pip install --upgrade gensim

In [2]:
from konlpy.tag import Kkma
import matplotlib.pyplot as plt
from tqdm import tqdm
from pandas import Panel
from sklearn.feature_extraction.text import TfidfVectorizer
from pandas import Panel

C:\anaconda3\lib\site-packages\ipykernel_launcher.py:4: FutureWarning: The Panel class is removed from pandas. Accessing it from the top-level namespace will also be removed in the next version
  after removing the cwd from sys.path.
C:\anaconda3\lib\site-packages\ipykernel_launcher.py:6: FutureWarning: The Panel class is removed from pandas. Accessing it from the top-level namespace will also be removed in the next version
  


In [10]:
from Brunch_data import *

In [11]:
meta = pd.read_json('C:/Users/eunice/dss_workspace/MLproject/data/metadata.json', lines=True)
read_file_lst = glob.glob('C:/Users/eunice/dss_workspace/MLproject/data/read\*')
maga = pd.read_json('C:/Users/eunice/dss_workspace/MLproject/data/magazine.json', lines=True)
us = pd.read_json('C:/Users/eunice/dss_workspace/MLproject/data/users.json', lines=True)

In [12]:
a = Data(meta, read_file_lst, maga, us)
me_df, r_df, mag_df, us_df = a.data_preprocessing()
# 2/15 - 3/31 train 데이터
train = a.train_data()

In [15]:
# article_id, keyword_list
key = a.train_keyword_list()

In [16]:
# readers별 article list와 articlle count가 있는 df :ra
ra_list_df = Read_article_outline_remove(train)
ra = ra_list_df.read_article_list()
# up = ra_list_df.upper_fence_remove()
# 5 이상 upper fence 밑으로 정리
# t3 = article_count_division_3(up)

In [17]:
upper_fence_df = ra[(ra['article_id_count']>=9) & (ra['article_id_count']<=64)]

In [94]:
# Doc2vec 실행을 위한 genism 설치
# !pip install --upgrade gensim

  Created wheel for smart-open: filename=smart_open-3.0.0-py3-none-any.whl size=107102 sha256=2f56b322270854ce7bca2038fa9addc67f471ab5367c7e98c9b40f01d85e5612
  Stored in directory: c:\users\eunice\appdata\local\pip\cache\wheels\83\a6\12\bf3c1a667bde4251be5b7a3368b2d604c9af2105b5c1cb1870
Successfully built smart-open
  Attempting uninstall: Cython
    Found existing installation: Cython 0.29.15
    Uninstalling Cython-0.29.15:
      Successfully uninstalled Cython-0.29.15


# Doc2Vec

## 독자 tag list doc2vec

In [13]:
from gensim.models.doc2vec import Doc2Vec, TaggedDocument

### 독자별 주로 읽은 글 태그 리스트 정리

In [25]:
reader_klist_df = train.groupby('readers_id')['keyword_list'].agg('sum')

In [30]:
reader_klist_df = pd.DataFrame(reader_klist_df)
reader_klist_df.reset_index(inplace=True)

### Doc2Vec 시작

In [32]:
# 한 독자의 리스트를 하나의 document로 보고, 독자 id를 문서 제목으로 봄
tags = reader_klist_df['keyword_list'].index
words = reader_klist_df['keyword_list'].values

In [33]:
doc_df = reader_klist_df[['readers_id', 'keyword_list']].values.tolist()

In [35]:
reader_klist_df[['readers_id', 'keyword_list']].values.tolist()

[['#0000fdba8f35c76eacab74c5c6bc7f1a',
  ['책소개', '도서', '에세이', '감동', '공감', '캘리그라피', '여행', '동행', '여행지']],
 ['#00034a8380a75a3b5787606a7f418525', ['방송작가', '운동', '스트레스']],
 ['#000474bba0c00c70e12ac7cfc3d04553',
  ['브런치', '시사회', '브런치무비패스', '최저가', '가격비교', '실전', '이직', '스타트업', '커리어']],
 ['#00050506dfe68410df8f26ca57bcce1e', ['디즈니', '영화리뷰', '뮤지컬']],
 ['#0008d577aa7bf5315b060fa9b09ad626', ['요리이야기', '하와이', '퇴사']],
 ['#000c82417339e173dbed1e413e9c15e0',
  ['브런치',
   '시사회',
   '브런치무비패스',
   '브런치',
   '시사회',
   '브런치무비패스',
   '시',
   '에세이',
   '나들이',
   '시',
   '에세이',
   '나들이',
   '스쿠버다이빙',
   '세계여행',
   '나들이',
   '호텔',
   '회장',
   '봄나들이']],
 ['#000c9b7827aba665e4c957f4223629fc',
  ['고양이',
   '길고양이',
   '반려동물',
   '직장인',
   '처세술',
   '회사원',
   '독서',
   '엄마',
   '지옥철',
   '테크놀로지',
   '온라인',
   '미용실',
   '엄마',
   '아빠']],
 ['#000dabfc8c46550c08aa040d351c886a', ['브런치', '시사회', '브런치무비패스']],
 ['#000f41ee06f84a2c46ee56b300f74fc0',
  ['스쿼트', '다이어트', '하체운동', '스쿼트', '근력', '운동']],
 ['#000fe61478d384d09f3bcdd0c2f

In [38]:
tagged_data = [TaggedDocument(words=_d, tags=[uid]) for uid, _d in doc_df]

### Doc2Vec model build

In [39]:
max_epochs=10

model = Doc2Vec(window=10,
               size=150,
               alpha=0.025,
               min_alpha=0.025,
               min_count=2,
               dm=1,
               negative=3,
               seed=9999)

model.build_vocab(tagged_data)

### Doc2Vec model 학습

In [40]:
for epoch in range(max_epochs):
    print('iteration {0}'.format(epoch))
    model.train(tagged_data, 
               total_examples=model.corpus_count,
               epochs=model.iter)
    
    model.alpha -= 0.002
    model.min_alpha=model.alpha

iteration 0
iteration 1
iteration 2
iteration 3
iteration 4
iteration 5
iteration 6
iteration 7
iteration 8
iteration 9


### 문장으로 유사한 독자 취향 찾아내기

In [41]:
model.random.seed(9999)

doc_list = '호주 유럽 프랑스 영국 비행기 티켓팅'.split(' ')
inferred_vector = model.infer_vector(doc_list)
return_docs = model.docvecs.most_similar(positive=[inferred_vector], topn=5)
for rd in return_docs:
    for des in reader_klist_df[reader_klist_df['readers_id'] == rd[0]]['keyword_list']:
        print(rd[0], rd[1], des)

#3ac8b92fe86d1cf0ac0c0c03ddeab60e 0.2586003243923187 []
#8bf0878d993261de73299a9843183eeb 0.2330915629863739 ['향수', '향기', '인도', '세계일주', '바라나시', '퇴사', '직장인', '생존', '치아건강', '치아관리', '건강']
#6ad4d1c3df0bd4cc7712517e970dd671 0.225701704621315 ['인터뷰', '작가', '아나운서', '마케팅', '콘텐츠', 'IoT', '클래스', '발레', '남성', '여행', '캐나다', '토론토', '마케팅', '위메프', '애드테크', '노키즈존', '사회문제', '실리콘밸리', '관리자', '조직', '실무', '여행', '호텔', '중국', '영어', '영어공부', '한국', '영국', '예술', '런던']
#23e9060191275d7bd885bf807d70c61c 0.2239549607038498 ['환경보호', '환경오염', 'TED', '봉사활동', '스케줄', '달력', '브런치', '시사회', '브런치무비패스']
#7e26a70683642e55a856414197efd7e6 0.21680457890033722 []


### 독자 간 유사도 확인하기

In [44]:
readers_id=[]
similarity=[]
keyword_list=[]
return_docs = model.docvecs.most_similar('#33620f077b18c9de5e68eee061a59705', topn=50)
for rd in return_docs:
    for des in reader_klist_df[reader_klist_df['readers_id'] == rd[0]]['keyword_list']:
        readers_id.append(rd[0])
        similarity.append(rd[1])
        keyword_list.append(des)

pd.DataFrame({'readers_id':readers_id, 'similarity':similarity, 'keyword_list':keyword_list})

readers_id  similarity  \
0   #247767f34250e6df8d3d9fee023b1525    0.962189   
1   #01544b827039024fbe3f71de88d3f100    0.960209   
2   #0b16218f957a9194e959351eb77eb6e0    0.960054   
3   #bbde97abfcba1e6ad7fb475df61b3408    0.956380   
4   #e26ea1cb3ebb57134a268cecca50b4d0    0.955343   
5   #15145e515548e5d27d9202f659f8b5c1    0.954777   
6   #3efa6d716fbc1ee77a993c147a281be8    0.953060   
7   #45b3fe1a0f3f487e7e0c1b434657bc39    0.952175   
8   #bb7312e7d38b214ced76dedf958eec1c    0.951326   
9   #ffebdf64f9cd0bbcd7725f641ceb2d0b    0.951283   
10  #4a9629c44a092bf06854fa69e50c084f    0.950793   
11  #231f9af02bbc736d09b2549db53de3d0    0.950642   
12  #589cf089deb0f2237d5842bb901f4b8a    0.950286   
13  #b77598fb74e470b99cadd503538405ca    0.949574   
14  #67c675a84f66f7ab1959591cf4ababa2    0.948867   
15  #5f784732b300cadd220de015f7689b81    0.948722   
16  #ab0bfbc01a6c12a87b23afa0815b100e    0.948640   
17  #c4d6a4c6b619c7f355aa1980be9c6ee8    0.947786   
18  #44efe708c75319f80df56b3f9a845eee    0.947594   
19  #e5c4e445ec1c755687f9093ed4237f36    0.947394   
20  #11110147576ded52948c72763fbd3981    0.946462   
21  #a076a2507779e60dfccfe4bdfaf4ebe6    0.945940   
22  #d5312cc8632a2b087370e3832c8c8cad    0.945406   
23  #840c17a88a33cf56373a366d65c5ab49    0.945374   
24  #ef9f247720cf01338a614f8cf6c49d72    0.945332   
25  #2320871965507ee06483a14da538de68    0.945188   
26  #ee62e22d5f531c0243d1a1ba9b363dcd    0.944964   
27  #8cc3161c1ca438534169c862a108227d    0.944754   
28  #fd5fdc01b9178c35861dc1573b3c163d    0.944276   
29  #907aea105133021bc8928faaf780838f    0.944260   
30  #2121a7038c19429501b847185aae1ff8    0.943368   
31  #6ac47883187aba639d75d237d0e66f0a    0.943145   
32  #8c6149ccf24fd0a34294c3b98f17b0ca    0.943108   
33  #173c8853c8a51038fecb6b331091a31f    0.943043   
34  #ec35ea6e298d523c195c4ceb486bd6ae    0.942549   
35  #21d4cde410bde8a219d9a689b1eb4c72    0.941063   
36  #29a428a1e32d8cd6198a1fa4c5be6ce5    0.940703   
37  #7d51d8c74257e011efbdc775be44f2c9    0.940608   
38  #027b81eb5adc0a0860d93b5e10e0ded9    0.940058   
39  #6f864ef75f532ca5b35ee9f74163a795    0.939915   
40  #2803737c7da2177a98b692f6dbd78cb6    0.939763   
41  #ed19011ba7439dfcdca0ef7fdf75c07f    0.938922   
42  #80c846f8d7f55fc96553ed696ff87eda    0.938715   
43  #c6c23b5618adbf540ae4d375d4534723    0.938420   
44  #84d972062aa61cd522dce3eb72642d69    0.938343   
45  #cd25cfa362e4ecacd4ee9ec3a330c212    0.937187   
46  #0ff9e1ae857e47c6c6584a2d72f0a8f2    0.937184   
47  #e9cd35532a02fb4a91b8104ef211c2cc    0.937137   
48  #4dfd834ee7bd3b753a1040fda1a6ca18    0.936916   
49  #688346a21bd0f79e82d89703a9100781    0.936389   

                                         keyword_list  
0                                      [육아, 결혼, 시어머니]  
1                                      [육아, 결혼, 시어머니]  
2                       [육아, 결혼, 시어머니, lg전자, 마케팅, 전략]  
3                                      [결혼, 육아, 시어머니]  
4                                      [육아, 결혼, 시어머니]  
5   [육아, 결혼, 시어머니, 스타벅스, 마케팅, 프랜차이즈, 무인양품, 브랜드, 물건...  
6                                      [육아, 결혼, 시어머니]  
7      [오키나와, 역사, 세계여행, 육아, 결혼, 시어머니, 점심, 도시락, 프랑스학교]  
8                       [육아, 결혼, 시어머니, lg전자, 마케팅, 전략]  
9   [육아, 결혼, 시어머니, 브런치, 시사회, 브런치무비패스, 브런치, 시사회, 브런...  
10                                     [시어머니, 결혼, 육아]  
11                      [육아, 결혼, 시어머니, lg전자, 마케팅, 전략]  
12                                     [육아, 결혼, 시어머니]  
13                                     [시어머니, 결혼, 육아]  
14                                     [육아, 결혼, 시어머니]  
15                                     [육아, 결혼, 시어머니]  
16                                     [육아, 결혼, 시어머니]  
17                                     [육아, 결혼, 시어머니]  
18                  [육아, 결혼, 시어머니, 디자이너, 디자인, 그래픽디자인]  
19                                     [시어머니, 결혼, 육아]  
20                                     [육아, 결혼, 시어머니]  
21                       [육아, 결혼, 시어머니, 출판, 출판계약, 계약]  
22                                 

In [43]:
# test reader
reader_klist_df[reader_klist_df['readers_id'] == '#33620f077b18c9de5e68eee061a59705']['keyword_list'].iloc[0]

['육아', '결혼', '시어머니']

## 작가 태그리스트 Doc2vec

### 작가별 주로 쓴 글 태그리스트 정리하기

In [49]:
# 1. 작가id와 아티클id를 포함한 df 생성 
author_df = meta[['author_id', 'article_id']]
author_df

author_id        article_id
0             @bookdb       @bookdb_782
1          @kohwang56     @kohwang56_81
2        @hannahajink    @hannahajink_4
3       @bryceandjuli  @bryceandjuli_88
4        @mijeongpark   @mijeongpark_34
...               ...               ...
643099        @uxstar        @uxstar_24
643100    @reading15m   @reading15m_575
643101       @hje3884      @hje3884_118
643102  @julieleekgep  @julieleekgep_12
643103  @julieleekgep  @julieleekgep_13

[643104 rows x 2 columns]

In [51]:
# 2. 작가id로 그룹바이, keyword list sum해서 전체 키워드리스트 도출
author_keyword = train.groupby('author_id')['keyword_list'].agg('sum')

In [52]:
author_keyword_df = pd.DataFrame(author_keyword)
author_keyword_df

keyword_list
author_id                                                       
@00books                                            [블루, 농민, 도쿄]
@01023920600                                                  []
@01026856762   [행복, 선택, 가족, 부모교육, 학교폭력, 가정, 부모교육, 학교폭력, 가정, 부...
@01038273527   [신용카드, 재테크, 부자, 신용카드, 재테크, 부자, 신용카드, 재테크, 부자, ...
@01archive     [영화, 사랑, 감정, 영화, 천재, 음악, 영화, 사랑, 영화, 사랑, 영화, 사...
...                                                          ...
@zzing-gu      [공감에세이, 글쓰기, 시, 공감에세이, 글쓰기, 시, 공감에세이, 글쓰기, 시, ...
@zzintta       [웹툰, 웹소설, 좀비, 웹툰, 웹소설, 좀비, 웹툰, 웹소설, 좀비, 웹툰, 웹소...
@zziraci                [중국, 세미나, 지식인, 독서, 원고, 중국, 마오, 마르크스, 중국]
@zzolmarkb6sm  [인테리어, 사진전, 중년, 사랑, 청소년, 감성에세이, 공감에세이, 육아, 초등교...
@zzongali                                [기억, 배신, 에세이, 글쓰기, 에세이]

[5825 rows x 1 columns]

In [55]:
author_keyword_df.reset_index(inplace=True)

In [76]:
# 3. 키워드 형태소 분석 

In [57]:
author_keyword_df

author_id                                       keyword_list
0          @00books                                       [블루, 농민, 도쿄]
1      @01023920600                                                 []
2      @01026856762  [행복, 선택, 가족, 부모교육, 학교폭력, 가정, 부모교육, 학교폭력, 가정, 부...
3      @01038273527  [신용카드, 재테크, 부자, 신용카드, 재테크, 부자, 신용카드, 재테크, 부자, ...
4        @01archive  [영화, 사랑, 감정, 영화, 천재, 음악, 영화, 사랑, 영화, 사랑, 영화, 사...
...             ...                                                ...
5820      @zzing-gu  [공감에세이, 글쓰기, 시, 공감에세이, 글쓰기, 시, 공감에세이, 글쓰기, 시, ...
5821       @zzintta  [웹툰, 웹소설, 좀비, 웹툰, 웹소설, 좀비, 웹툰, 웹소설, 좀비, 웹툰, 웹소...
5822       @zziraci           [중국, 세미나, 지식인, 독서, 원고, 중국, 마오, 마르크스, 중국]
5823  @zzolmarkb6sm  [인테리어, 사진전, 중년, 사랑, 청소년, 감성에세이, 공감에세이, 육아, 초등교...
5824      @zzongali                            [기억, 배신, 에세이, 글쓰기, 에세이]

[5825 rows x 2 columns]

### Doc2Vec 시작

In [60]:
tags_author = author_keyword_df['keyword_list'].index
words_author = author_keyword_df['keyword_list'].values

In [61]:
author_keyword_df.reset_index(inplace=True)

In [62]:
doc_df = author_keyword_df[['author_id', 'keyword_list']].values.tolist()
doc_df

[['@00books', ['블루', '농민', '도쿄']],
 ['@01023920600', []],
 ['@01026856762',
  ['행복',
   '선택',
   '가족',
   '부모교육',
   '학교폭력',
   '가정',
   '부모교육',
   '학교폭력',
   '가정',
   '부모교육',
   '학교폭력',
   '가정',
   '부모교육',
   '학교폭력',
   '가정',
   '부모교육',
   '학교폭력',
   '가정',
   '부모교육',
   '학교폭력',
   '가정',
   '부모교육',
   '학교폭력',
   '가정',
   '부모교육',
   '학교폭력',
   '가정',
   '부모교육',
   '학교폭력',
   '가정',
   '부모교육',
   '학교폭력',
   '가정',
   '부모교육',
   '학교폭력',
   '가정',
   '부모교육',
   '학교폭력',
   '가정',
   '부모교육',
   '학교폭력',
   '가정',
   '부모교육',
   '학교폭력',
   '가정',
   '부모교육',
   '학교폭력',
   '가정',
   '부모교육',
   '학교폭력',
   '가정',
   '부모교육',
   '학교폭력',
   '가정',
   '부모교육',
   '학교폭력',
   '가정',
   '부모교육',
   '학교폭력',
   '가정',
   '부모교육',
   '학교폭력',
   '가정',
   '부모교육',
   '학교폭력',
   '가정',
   '부모교육',
   '학교폭력',
   '가정',
   '부모교육',
   '학교폭력',
   '가정',
   '부모교육',
   '학교폭력',
   '가정',
   '부모교육',
   '학교폭력',
   '가정',
   '부모교육',
   '학교폭력',
   '가정',
   '부모교육',
   '학교폭력',
   '가정',
   '부모교육',
   '학교폭력',
   '가정',
   '부모교육',
   '학교폭력',
   '가정'

In [63]:
tagged_data = [TaggedDocument(words=_d, tags=[uid]) for uid, _d in doc_df]

### Doc2Vec model build

In [64]:
max_epochs=10

model = Doc2Vec(window=10,
               size=150,
               alpha=0.025,
               min_alpha=0.025,
               min_count=2,
               dm=1,
               negative=3,
               seed=9999)

model.build_vocab(tagged_data)

### Doc2Vec model 학습

In [65]:
for epoch in range(max_epochs):
    print('iteration {0}'.format(epoch))
    model.train(tagged_data, 
               total_examples=model.corpus_count,
               epochs=model.iter)
    
    model.alpha -= 0.002
    model.min_alpha=model.alpha

iteration 0
iteration 1
iteration 2
iteration 3
iteration 4
iteration 5
iteration 6
iteration 7
iteration 8
iteration 9


### 문장으로 유사한 글소재의 작가 찾아내기

In [73]:
model.random.seed(9999)

doc_list = '호주 유럽 프랑스 영국 비행기 티켓팅'.split(' ')
inferred_vector = model.infer_vector(doc_list)
return_docs = model.docvecs.most_similar(positive=[inferred_vector], topn=5)
for rd in return_docs:
    for des in author_keyword_df[author_keyword_df['author_id'] == rd[0]]['keyword_list']:
        print(rd[0], rd[1], des)

@dagrim1202 0.7435606122016907 ['영화', '영국', '여왕']
@lisayunseonpark 0.6703714728355408 ['워킹홀리데이', '네덜란드', '워홀', '여행', '덴마크', '워홀', '코펜하겐', '덴마크', '유럽']
@jieunjoysong 0.634747326374054 ['유럽', '교환학생', '영국', '이해', '사람', '세상']
@bonapark 0.6185988783836365 ['박물관', '영국', '유럽']
@ykimkim 0.6155397295951843 ['박사과정', '독일유학', '공부', '영국', '유학생활', '맨체스터']


### 작가 간 유사도 확인하기

In [74]:
author_id=[]
similarity=[]
keyword_list=[]
return_docs = model.docvecs.most_similar('@youjinlee4p6f', topn=50)
for rd in return_docs:
    for des in author_keyword_df[author_keyword_df['author_id'] == rd[0]]['keyword_list']:
        author_id.append(rd[0])
        similarity.append(round(rd[1],2))
        keyword_list.append(des)

pd.DataFrame({'author_id':author_id, 'similarity':similarity, 'keyword_list':keyword_list})

author_id  similarity  \
0           @13july        0.65   
1     @sombrablanca        0.56   
2        @concepter        0.56   
3          @ayogara        0.55   
4        @mareykrap        0.54   
5         @chatbete        0.53   
6        @stayfolio        0.52   
7         @merryseo        0.51   
8        @grumsarah        0.50   
9        @john-ater        0.49   
10       @white2804        0.49   
11            @bong        0.49   
12           @heean        0.48   
13        @jinsu611        0.48   
14        @tumblbug        0.48   
15            @jino        0.47   
16     @coologi0812        0.47   
17       @mcwannabe        0.47   
18          @cwhboy        0.47   
19      @bbangdream        0.46   
20     @duddlweo7py        0.46   
21  @avocadolistens        0.46   
22       @peacheeks        0.46   
23      @keentoknow        0.46   
24          @kkw119        0.46   
25         @jo-hnjn        0.46   
26  @valuedeveloper        0.45   
27      @personalab        0.45   
28    @sangolhyewon        0.45   
29    @wouldyoulike        0.45   
30     @leesang3002        0.45   
31     @aprilispark        0.45   
32        @dajimade        0.45   
33         @kimseom        0.45   
34         @bdg0606        0.45   
35         @kospo60        0.44   
36      @cute12soul        0.44   
37         @khs8842        0.44   
38  @wildflower1212        0.44   
39         @coldsky        0.44   
40         @ihanvin        0.44   
41            @uuil        0.44   
42    @changgoseoul        0.44   
43         @rab4040        0.44   
44       @kimjiyoun        0.44   
45        @artnomad        0.44   
46        @edigna01        0.44   
47         @blade31        0.44   
48    @younggeumcho        0.43   
49         @3000won        0.43   

                                         keyword_list  
0   [그림일기, 일러스트레이션, 정전, 그림일기, 일러스트레이션, 정전, 그림일기, 일...  
1   [캘리그라피, 그림일기, 글쓰기, 캘리그라피, 그림일기, 글쓰기, 캘리그라피, 그림...  
2   [책방, 직장인, 여행, 여행, 을지로, 사진, 디자인, 현대카드, 북촌, 디자인,...  
3   [일상, 자영업, 동네서점, 책방, 자영업, 모임, 책방, 자영업, 모임, 책방, ...  
4   [뮤직비디오, 일러스트레이션, 이태원, 뮤직비디오, 일러스트레이션, 이태원, 뮤직비...  
5   [책방일기, 책방, 에코백, 책방일기, 독서, 영상, 책방일기, 독서, 영상, 책방...  
6   [캠핑, 제주도, 여행, 자연, 여행, 향기, 자연, 여행, 향기, 자연, 여행, ...  
7   [인문학, 독서, 일러스트, 인문학, 독서, 일러스트, 인문학, 독서, 일러스트, ...  
8   [손그림, 편지, 일러스트, 편지, 손편지, 일러스트, 편지, 손편지, 일러스트, ...  
9   [자기소개, 소개, 하루키, 자기소개, 소개, 하루키, 자기소개, 소개, 하루키, ...  
10  [종이잡지클럽, 잡지, 매거진, 종이잡지클럽, 잡지, 매거진, 종이잡지클럽, 잡지,...  
11  [박진영, 아이돌, 박진영, 아이돌, 박진영, 아이돌, 박진영, 아이돌, 박진영, ...  
12  [아이돌, 팬덤, 아이돌, 팬덤, 아이돌, 팬덤, 아이돌, 팬덤, 아이돌, 팬덤, ...  
13   [생각, 사고, 생각, 사고, 생각, 사고, 생각, 사고, 생각, 사고, 생각, 사고]  
14  [트렌드, 펀딩, 콘텐츠, 트렌드, 펀딩, 콘텐츠, 트렌드, 펀딩, 콘텐츠, 트렌드...  
15                              [코타키나발루, 해외여행, 뮤직비디오]  
16                                         [그림일기, 일상]  
17  [박진영, 트와이스, 아이돌, 프로듀스101, 걸그룹, 아이돌, 프로듀스101, 걸...  
18  [백업, 하드, 나스, 백업, 하드, 나스, 백업, 하드, 나스, 백업, 하드, 나...  
19      [에세이, 에세이클럽, 일요일, 에세이클럽, 일요일, 에세이클럽, 일요일, 독서]  
20                                              [드로잉]  
21  [내한공연, 공연, 음악, 내한공연, 공연, 음악, 내한공연, 공연, 음악, 내한공...  
22                                         [그림여행, 여행]  
23  [생각, 사고, 생각, 사고, 생각, 사고, 생각, 사고, 생각, 사고, 생각, 사...  
24  [서울, 외로움, 관계, 서울, 외로움, 관계, 서울, 외로움, 관계, 서울, 외로...  
25  [복수초, 식물, 도감, 여행, 연필, 정원, 여행, 연필, 정원, 여행, 연필, ...  
26                             [걸그룹, 컨셉, 작곡, 히트곡, 힙합]  
27  [직장인, 몸값, 법칙, 직장인, 몸값, 법칙, 직장인, 몸값, 법칙, 직장인, 몸...  
28  [메주, 된장, 미세먼지, 메주, 된장, 미세먼지, 메주, 된장, 미세먼지, 메주,...  
29  [시리우스, 우주, 천문학, 시리우스, 우주, 천문학, 시리우스, 우주, 천문학, ...  
30  [카페, 문화, 의문, 카페, 문화, 의문, 카페, 문화, 의문, 카페, 문화, 의...  
31  [캄보디아여행, 혼자여행, 여행기, 캄보디아여행, 혼자여행, 여행기, 캄보디아여행,...  
32  [아이돌, 케이팝, 대중음악, 아이돌, 케이팝, 대중음악, 아이돌, 케이팝, 대중음...  
33             [아재, 아재개그, 문화, 청춘예찬, 연극, 일기, 에세이, 서른살]  
34  [사진전, 전시, 전시리뷰, 사진전, 전시, 전시리뷰, 사진전, 전시, 전시리뷰, ...  
35                                           [복권, 희망]  
36  [음악, 노래, 아침, 음악, 노래, 아침, 음악, 노래, 아침, 음악, 노래, 아...  
37  [드로잉, 강화도, 카페, 드로잉, 강화도, 카페, 드로잉, 강화도, 카페, 드로잉...  
38  [일러스트, 글귀, 위로, 일러스트, 글귀, 위로, 일러스트, 글

In [75]:
author_keyword_df[author_keyword_df['author_id'] == '@youjinlee4p6f']['keyword_list'].iloc[0]

['책방',
 '그림일기',
 '일러스트레이션',
 '책방',
 '그림일기',
 '일러스트레이션',
 '책방',
 '그림일기',
 '일러스트레이션',
 '책방',
 '그림일기',
 '일러스트레이션',
 '책방',
 '그림일기',
 '일러스트레이션',
 '책방',
 '그림일기',
 '일러스트레이션',
 '책방',
 '그림일기',
 '일러스트레이션',
 '책방',
 '그림일기',
 '일러스트레이션',
 '책방',
 '그림일기',
 '일러스트레이션',
 '책방',
 '그림일기',
 '일러스트레이션',
 '책방',
 '그림일기',
 '일러스트레이션',
 '책방',
 '그림일기',
 '일러스트레이션',
 '책방',
 '그림일기',
 '일러스트레이션',
 '책방',
 '그림일기',
 '일러스트레이션',
 '책방',
 '그림일기',
 '일러스트레이션',
 '책방',
 '그림일기',
 '일러스트레이션',
 '책방',
 '그림일기',
 '일러스트레이션',
 '책방',
 '그림일기',
 '일러스트레이션',
 '책방',
 '그림일기',
 '일러스트레이션',
 '책방',
 '그림일기',
 '일러스트레이션',
 '책방',
 '그림일기',
 '일러스트레이션',
 '책방',
 '그림일기',
 '일러스트레이션',
 '책방',
 '그림일기',
 '일러스트레이션',
 '책방',
 '그림일기',
 '일러스트레이션',
 '책방',
 '그림일기',
 '일러스트레이션',
 '책방',
 '그림일기',
 '일러스트레이션',
 '책방',
 '그림일기',
 '일러스트레이션',
 '책방',
 '그림일기',
 '일러스트레이션',
 '책방',
 '그림일기',
 '일러스트레이션',
 '책방',
 '그림일기',
 '일러스트레이션',
 '책방',
 '그림일기',
 '일러스트레이션',
 '책방',
 '그림일기',
 '일러스트레이션',
 '책방',
 '그림일기',
 '일러스트레이션',
 '책방',
 '그림일기',
 '일러스트레이션',
 '책방',
 '그림일기',
 '일러스트레이션',
 '책방',
 '그림일기',
 '일러